In [192]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [193]:
from src.SWATPollution import SWATPollution
from pathlib import Path
from src.pollution_utils import generate_pollution_observations, observacions_from_conca
import pandas as pd
import geopandas as gpd
import geoviews as gv

In [194]:
contaminant = 'Ciprofloxacina'
conca = 'besos'

In [195]:
cwd = Path('C:\\Users\\jsalo\\Desktop\\ICRA\\traca_contaminacio\\traca_contaminacio')
txtinout_folder = cwd/'data'/'txtinouts'/'tmp'/contaminant/f"{conca}"
channels_geom_path = cwd/'data'/'rivs1'/'canals_tot_ci.shp'
lod_path = cwd / 'data' / 'lod.xlsx'
recall_points_path = cwd.parent / 'traca' / 'traca' / 'inputs compound generator' / 'inputs' / 'recall_points.xlsx'

In [196]:
recall_points_df = pd.read_excel(recall_points_path)
edars = recall_points_df[recall_points_df['conca'] == conca][['lat', 'lon', 'edar_code']].dropna()

In [197]:
observacions = generate_pollution_observations(contaminant)
df = observacions_from_conca(channels_geom_path, observacions, conca)


In [198]:
first_observation = df.year.min()
year_end = 2025
year_start = max(first_observation-3, 2000) #3 years warm-up
warmup = max(1, first_observation - year_start)

In [199]:
lod_df = pd.read_excel(lod_path, index_col=0)
lod = lod_df.loc[contaminant, 'LOD (mg/L)']


In [200]:
#mg/l
llindars = {
    'Venlafaxina': 6*1e-6,
    'Diuró': 200*1e-6,
    'Triclorometà': 2500*1e-6,
    'Ciprofloxacina': 89*1e-6,
}

In [201]:

swatpy = SWATPollution( 
        conca, 
        contaminant, 
        txtinout_folder = txtinout_folder,
        channels_geom_path = channels_geom_path,
        run = False,
        observacions = observacions.copy(),
        lod = lod,
        year_start = year_start,
        year_end = year_end,
        warmup = warmup
)


In [202]:
#rmse
swatpy.get_error()  

0.9767256786848142

In [203]:
swatpy.scatter_plot()

In [204]:
df = swatpy.df
df

month   day    year  gis_id       pollutant      mg_l  flo_out  \
0         1.0   1.0  2019.0     1.0  Ciprofloxacina  0.000016   0.6415   
1         1.0   2.0  2019.0     1.0  Ciprofloxacina  0.000017   0.6335   
2         1.0   3.0  2019.0     1.0  Ciprofloxacina  0.000017   0.6226   
3         1.0   4.0  2019.0     1.0  Ciprofloxacina  0.000017   0.6132   
4         1.0   5.0  2019.0     1.0  Ciprofloxacina  0.000017   0.6035   
...       ...   ...     ...     ...             ...       ...      ...   
534408   12.0  27.0  2025.0   209.0  Ciprofloxacina  0.000163   0.1585   
534409   12.0  28.0  2025.0   209.0  Ciprofloxacina  0.000163   0.1586   
534410   12.0  29.0  2025.0   209.0  Ciprofloxacina  0.000163   0.1579   
534411   12.0  30.0  2025.0   209.0  Ciprofloxacina  0.000163   0.1582   
534412   12.0  31.0  2025.0   209.0  Ciprofloxacina  0.000163   0.1585   

         tot_out_mg  Channel  \
0        910.540000        1   
1        910.542100        1   
2        910.539700        1   
3        910.542400        1   
4        910.543900        1   
...             ...      ...   
534408  2229.001063      209   
534409  2229.001063      209   
534410  2229.001063      209   
534411  2229.001063      209   
534412  2229.001063      209   

                                                 geometry  layer       Date  
0       LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2019-01-01  
1       LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2019-01-02  
2       LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2019-01-03  
3       LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2019-01-04  
4       LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2019-01-05  
...                                                   ...    ...        ...  
534408  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2025-12-27  
534409  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2025-12-28  
534410  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2025-12-29  
534411  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2025-12-30  
534412  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2025-12-31  

[534413 rows x 12 columns]

In [205]:
import numpy as np
import plotly.express as px
flows = swatpy.df.groupby('Date').flo_out.mean()
fig = px.line(x=flows.index, y=np.log2(flows.values))
fig.show()

In [206]:
today = pd.to_datetime('2022-12-25')
flow_by_day = flows
flow_by_day = flow_by_day[flow_by_day.index >= today]

In [207]:
pollution_today = df[df.Date == today].copy()
pollution_today

month   day    year  gis_id       pollutant      mg_l   flo_out  \
1454     12.0  25.0  2022.0     1.0  Ciprofloxacina  0.000171  0.061550   
4011     12.0  25.0  2022.0     2.0  Ciprofloxacina  0.000240  0.024670   
6568     12.0  25.0  2022.0     3.0  Ciprofloxacina  0.000219  0.027050   
9125     12.0  25.0  2022.0     4.0  Ciprofloxacina  0.000168  0.062780   
11682    12.0  25.0  2022.0     5.0  Ciprofloxacina       NaN  0.000000   
...       ...   ...     ...     ...             ...       ...       ...   
523082   12.0  25.0  2022.0   205.0  Ciprofloxacina       NaN  0.000000   
525639   12.0  25.0  2022.0   206.0  Ciprofloxacina  0.000000  0.008065   
528196   12.0  25.0  2022.0   207.0  Ciprofloxacina  0.000000  0.003608   
530753   12.0  25.0  2022.0   208.0  Ciprofloxacina  0.000164  0.157500   
533310   12.0  25.0  2022.0   209.0  Ciprofloxacina  0.000163  0.158500   

         tot_out_mg  Channel  \
1454     911.406628        1   
4011     511.930940        2   
6568     511.660990        3   
9125     910.611830        4   
11682      0.000000        5   
...             ...      ...   
523082     0.000000      205   
525639     0.000000      206   
528196     0.000000      207   
530753  2229.000531      208   
533310  2229.001063      209   

                                                 geometry  layer       Date  
1454    LINESTRING (2.70642 41.80019, 2.70642 41.80084...  besos 2022-12-25  
4011    LINESTRING (2.59920 41.75998, 2.59833 41.75998...  besos 2022-12-25  
6568    LINESTRING (2.58345 41.76450, 2.58345 41.76516...  besos 2022-12-25  
9125    LINESTRING (2.71510 41.81329, 2.71422 41.81394...  besos 2022-12-25  
11682   LINESTRING (2.66858 41.85239, 2.66770 41.85304...  besos 2022-12-25  
...                                                   ...    ...        ...  
523082  LINESTRING (2.76589 41.78594, 2.76676 41.78529...  besos 2022-12-25  
525639  LINESTRING (2.74395 41.79916, 2.74694 41.79782...  besos 2022-12-25  
528196  LINESTRING (2.14794 41.48160, 2.14707 41.48159...  besos 2022-12-25  
530753  LINESTRING (2.68052 41.78403, 2.68121 41.78435...  besos 2022-12-25  
533310  LINESTRING (2.68935 41.79177, 2.68988 41.79225...  besos 2022-12-25  

[209 rows x 12 columns]

In [240]:
flow_today = flow_by_day.loc[today]
flow_7 = flow_today * 0.93
#flow_18 = flow_today * 0.82
flow_18 = min(flow_by_day)

In [246]:
flow_7_df = flow_by_day[flow_by_day <= flow_7].head(1)
date_flow_7 = flow_7_df.index[0]

flow_18_df = flow_by_day[flow_by_day <= flow_18].head(1)
date_flow_18 = flow_18_df.index[0]

pollution_7 = df[df.Date == date_flow_7]
pollution_18 = df[df.Date == date_flow_18]

In [215]:
swatpy.visualise_concentration(day = date_flow_18.day, month = date_flow_18.month, year = date_flow_18.year)

:Overlay
   .Path.I  :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .Path.II :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .WMTS.I  :WMTS   [Longitude,Latitude]

In [216]:
swatpy.visualise_concentration(day = date_flow_7.day, month = date_flow_7.month, year = date_flow_7.year)

:Overlay
   .Path.I  :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .Path.II :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .WMTS.I  :WMTS   [Longitude,Latitude]

In [217]:
date_flow_7

Timestamp('2023-04-13 00:00:00')

In [218]:
date_flow_18

Timestamp('2025-06-13 00:00:00')

In [219]:
swatpy.visualise_concentration(day = today.day, month = today.month, year = today.year)

:Overlay
   .Path.I  :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .Path.II :Path   [Longitude,Latitude]   (month,day,year,gis_id,pollutant,mg_l,flo_out,tot_out_mg,Channel,layer,Date,date_str,color)
   .WMTS.I  :WMTS   [Longitude,Latitude]

In [220]:
diferencia_7 = pollution_7.merge(pollution_today[['gis_id', 'pollutant', 'mg_l', 'flo_out']], on = ['gis_id', 'pollutant'])
diferencia_7['flow_%'] = 100 * diferencia_7.flo_out_x / diferencia_7.flo_out_y
diferencia_7['concentration_%'] = 100 * diferencia_7.mg_l_x / diferencia_7.mg_l_y

In [221]:
from bokeh.models import HoverTool


gdf_7 = gpd.GeoDataFrame(diferencia_7[['geometry', 'flow_%']].dropna(), geometry='geometry')

atribute_map = gv.Path(
    gdf_7,
).opts(color='flow_%', show_legend=True, cmap = 'RdBu', colorbar=True, line_width=3, clim=(0, 200))

gdf_map = swatpy.gdf_map[(swatpy.gdf_map['Date'].dt.year == date_flow_7.year) & (swatpy.gdf_map['Date'].dt.month == date_flow_7.month) & (swatpy.gdf_map['Date'].dt.day == date_flow_7.day)]

"""
river = gv.Path(
    river_map,
).opts(tools=[hover], color='black', line_width=3, alpha=0.5)
"""

tiles = gv.tile_sources.CartoLight()

(atribute_map * tiles).opts(width=800, height=500)



:Overlay
   .Path.I :Path   [Longitude,Latitude]   (flow_%)
   .WMTS.I :WMTS   [Longitude,Latitude]

In [222]:
gdf_7 = gpd.GeoDataFrame(diferencia_7[['geometry', 'concentration_%']].dropna(), geometry='geometry')

atribute_map = gv.Path(
    gdf_7,
).opts(color='concentration_%', show_legend=True, cmap = 'coolwarm', colorbar=True, line_width=2.5, clim=(0, 200))

tiles = gv.tile_sources.CartoLight()  # You can choose from different tile sources


(atribute_map * tiles).opts(width=800, height=500)

:Overlay
   .Path.I :Path   [Longitude,Latitude]   (concentration_%)
   .WMTS.I :WMTS   [Longitude,Latitude]

In [223]:
diferencia_18 = pollution_18.merge(pollution_today[['gis_id', 'pollutant', 'mg_l', 'flo_out']], on = ['gis_id', 'pollutant'])
diferencia_18['flow_%'] = 100 * diferencia_18.flo_out_x / diferencia_18.flo_out_y
diferencia_18['concentration_%'] = 100 * diferencia_18.mg_l_x / diferencia_18.mg_l_y
diferencia_18

month   day    year  gis_id       pollutant    mg_l_x  flo_out_x  \
0      6.0  13.0  2025.0     1.0  Ciprofloxacina  0.000208   0.050670   
1      6.0  13.0  2025.0     2.0  Ciprofloxacina       inf   0.000000   
2      6.0  13.0  2025.0     3.0  Ciprofloxacina  0.003323   0.001776   
3      6.0  13.0  2025.0     4.0  Ciprofloxacina  0.000195   0.054040   
4      6.0  13.0  2025.0     5.0  Ciprofloxacina       NaN   0.000000   
..     ...   ...     ...     ...             ...       ...        ...   
204    6.0  13.0  2025.0   205.0  Ciprofloxacina       NaN   0.000000   
205    6.0  13.0  2025.0   206.0  Ciprofloxacina  0.000000   0.004101   
206    6.0  13.0  2025.0   207.0  Ciprofloxacina       NaN   0.000000   
207    6.0  13.0  2025.0   208.0  Ciprofloxacina  0.000184   0.139900   
208    6.0  13.0  2025.0   209.0  Ciprofloxacina  0.000182   0.142000   

      tot_out_mg  Channel                                           geometry  \
0     911.206626        1  LINESTRING (2.70642 41.80019, 2.70642 41.80084...   
1     507.465500        2  LINESTRING (2.59920 41.75998, 2.59833 41.75998...   
2     509.859600        3  LINESTRING (2.58345 41.76450, 2.58345 41.76516...   
3     910.611720        4  LINESTRING (2.71510 41.81329, 2.71422 41.81394...   
4       0.000000        5  LINESTRING (2.66858 41.85239, 2.66770 41.85304...   
..           ...      ...                                                ...   
204     0.000000      205  LINESTRING (2.76589 41.78594, 2.76676 41.78529...   
205     0.000000      206  LINESTRING (2.74395 41.79916, 2.74694 41.79782...   
206     0.000000      207  LINESTRING (2.14794 41.48160, 2.14707 41.48159...   
207  2229.000531      208  LINESTRING (2.68052 41.78403, 2.68121 41.78435...   
208  2229.001328      209  LINESTRING (2.68935 41.79177, 2.68988 41.79225...   

     layer       Date    mg_l_y  flo_out_y     flow_%  concentration_%  
0    besos 2025-06-13  0.000171   0.061550  82.323314       121.445615  
1    besos 2025-06-13  0.000240   0.024670   0.000000              inf  
2    besos 2025-06-13  0.000219   0.027050   6.565619      1517.723302  
3    besos 2025-06-13  0.000168   0.062780  86.078369       116.173191  
4    besos 2025-06-13       NaN   0.000000        NaN              NaN  
..     ...        ...       ...        ...        ...              ...  
204  besos 2025-06-13       NaN   0.000000        NaN              NaN  
205  besos 2025-06-13  0.000000   0.008065  50.849349              NaN  
206  besos 2025-06-13  0.000000   0.003608   0.000000              NaN  
207  besos 2025-06-13  0.000164   0.157500  88.825397       112.580415  
208  besos 2025-06-13  0.000163   0.158500  89.589905       111.619732  

[209 rows x 16 columns]

In [224]:
gdf_18 = gpd.GeoDataFrame(diferencia_7[['geometry', 'flow_%']].dropna(), geometry='geometry')

atribute_map = gv.Path(
    gdf_18,
).opts(color='flow_%', show_legend=True, cmap = 'RdBu', colorbar=True, line_width=2.5, clim=(0, 200))

tiles = gv.tile_sources.CartoLight()  # You can choose from different tile sources


(atribute_map * tiles).opts(width=800, height=500)

:Overlay
   .Path.I :Path   [Longitude,Latitude]   (flow_%)
   .WMTS.I :WMTS   [Longitude,Latitude]

In [225]:
gdf_18 = gpd.GeoDataFrame(diferencia_18[['geometry', 'concentration_%']].dropna(), geometry='geometry')

atribute_map = gv.Path(
    gdf_18,
).opts(color='concentration_%', show_legend=True, cmap = 'coolwarm', colorbar=True, line_width=2.5, clim=(0, 200))

tiles = gv.tile_sources.CartoLight()  # You can choose from different tile sources


(atribute_map * tiles).opts(width=800, height=500)

:Overlay
   .Path.I :Path   [Longitude,Latitude]   (concentration_%)
   .WMTS.I :WMTS   [Longitude,Latitude]

In [226]:
#incompliments ara
len(pollution_today[pollution_today.mg_l > llindars[contaminant]])

108

In [227]:
#incompliments 7%
len(pollution_7[pollution_7.mg_l > llindars[contaminant]])

110

In [228]:
#incompliments 18%
len(pollution_18[pollution_18.mg_l > llindars[contaminant]])

112

In [229]:
#mitjana ara
import numpy as np
pollution_today.mg_l.replace([np.inf, -np.inf], np.nan).dropna().mean()

0.00013390745232260112

In [230]:
#mitjana 7%
pollution_7.mg_l.replace([np.inf, -np.inf], np.nan).dropna().mean()

0.000741133868702767

In [231]:
#mitjana 18%
pollution_18.mg_l.replace([np.inf, -np.inf], np.nan).dropna().mean()

0.0002744176782481017